# CHAPTER 9. 텐서플로 시작하기 II

In [153]:
# 복습


---
## 9.8 모델 저장과 복원

- 모델 훈련을 시키고 나면 해당 모델을 다시 쓸 수 있어야한다.
  1. 다른 프로그램에서 사용
  2. 다른 모델과 비교 
  3. 훈련 중 문제가 생겨 다시 시작해야하는 경우
<br/><br/>
- 텐서플로우에서 모델을 저장하는 방법 <br/>
  : 모든 노드를 생성한 뒤 Saver 노드를 마지막에 추가한 뒤, 실행 단계에서 저장하고 싶을 때 Save() 호출
- 변수의 이름 등을 변경해서 저장하고 복원할 수 있음.

In [31]:
save_dir = "/Users/zoostar/Documents/git/hans_on_ml_link/saveModels/"

In [35]:
reset_graph()

n_epochs = 1000                                                                      
learning_rate = 0.01                                                                 

X = tf.constant(scaled_housing_data_plus_bias, dtype=tf.float32, name="X")           
y = tf.constant(housing.target.reshape(-1, 1), dtype=tf.float32, name="y")
theta = tf.Variable(tf.random_uniform([n + 1, 1], -1.0, 1.0, seed=42), name="theta")
y_pred = tf.matmul(X, theta, name="predictions")                                     
error = y_pred - y                                                                   
mse = tf.reduce_mean(tf.square(error), name="mse")                                   
optimizer = tf.train.GradientDescentOptimizer(learning_rate=learning_rate)           
training_op = optimizer.minimize(mse)                                                

init = tf.global_variables_initializer()
saver = tf.train.Saver() #Save 노드 추가
# saver = tf.train.Saver({"weights": theta})
with tf.Session() as sess:
    sess.run(init)

    for epoch in range(n_epochs):
        if epoch % 100 == 0:
            print("에포크", epoch, "MSE =", mse.eval())                                # 중간중간 체크포인트 모델 저장
            save_path = saver.save(sess, save_dir+"my_model.ckpt")
        sess.run(training_op)
    
    best_theta = theta.eval() # 학습 완료 후 최종 모델 저장
    save_path = saver.save(sess, save_dir+"my_model_final.ckpt")

에포크 0 MSE = 9.161542
에포크 100 MSE = 0.7145004
에포크 200 MSE = 0.56670487
에포크 300 MSE = 0.55557173
에포크 400 MSE = 0.5488112
에포크 500 MSE = 0.5436363
에포크 600 MSE = 0.53962904
에포크 700 MSE = 0.5365092
에포크 800 MSE = 0.53406775
에포크 900 MSE = 0.5321473


In [36]:
best_theta

array([[ 2.0685525 ],
       [ 0.8874027 ],
       [ 0.14401658],
       [-0.34770882],
       [ 0.36178368],
       [ 0.00393811],
       [-0.04269556],
       [-0.6614528 ],
       [-0.6375277 ]], dtype=float32)

<br/><br/>
- 모델을 복원하는 것은 restore 이용 (sess.run(init) 대신 restore)
- .meta 확장자의 파일에 그래프 구조를 저장하고, 이 구조를 읽어 들여 그래프를 복원하는 데 이용할 수 있음. 따라서 원래 코드를 보지 않고도 모든 모델을 복원 할 수 있다. 

In [38]:
with tf.Session() as sess:
    saver.restore(sess, save_dir+"my_model_final.ckpt")
    best_theta_restored = theta.eval()

INFO:tensorflow:Restoring parameters from /Users/zoostar/Documents/git/hans_on_ml_link/saveModels/my_model_final.ckpt


In [183]:
tf.get_default_graph().as_graph_def()

node {
  name: "X"
  op: "Const"
  attr {
    key: "dtype"
    value {
      type: DT_FLOAT
    }
  }
  attr {
    key: "value"
    value {
      tensor {
        dtype: DT_FLOAT
        tensor_shape {
          dim {
            size: 20640
          }
          dim {
            size: 9
          }
        }
        tensor_content: "\000\000\200?\244\020\026@\264m{?F\351 ?\241r\035\276\'ty\277\275%K\275\347\271\206?\201\366\251\277\000\000\200?cC\025@\227e\033\277\367q\247>\362\323\206\276B\207\\?\rw\275\275\022\207\205?\363R\251\277\000\000\200?~/\344?[\227\355?_\353\223?a\305H\275w\036R\277\265\263\323\274\250\355\204?\017\232\252\277\000\000\200?\365\326n?[\227\355?\267\273 >\232\035L\275j\032D\277\031&N\275\250\355\204?\235=\253\277\000\000\200?\320\nS\274[\227\355?\357}\260>M\310\006\275P\205B\277QW\257\275\250\355\204?\235=\253\277\000\000\200?9\027\263=[\227\355?\002\032\212\276\261Wp<\322\341d\277\334\211\267\275\250\355\204?\235=\253\277\000\000\200?\005\024\344\275[\227\355

In [134]:
np.allclose(best_theta, best_theta_restored)
#allclose : 두 배열이 허용오차 내에서 일치할 경우 True 리턴, 제대로 불러왔다는 뜻.

True

In [39]:
reset_graph()

with tf.Session() as sess:
    saver.restore(sess, save_dir+"my_model_final.ckpt")
    best_theta_restored = theta.eval()

INFO:tensorflow:Restoring parameters from /Users/zoostar/Documents/git/hans_on_ml_link/saveModels/my_model_final.ckpt


RuntimeError: The Session graph is empty.  Add operations to the graph before calling run().

In [41]:
reset_graph()

saver = tf.train.import_meta_graph(save_dir+"my_model_final.ckpt.meta")  # 그래프 구조를 로드합니다.
theta = tf.get_default_graph().get_tensor_by_name("theta:0") 

with tf.Session() as sess:
    saver.restore(sess, save_dir+"my_model_final.ckpt")  
    # 그래프 상태를 로드합니다.
    best_theta_restored = theta.eval()

INFO:tensorflow:Restoring parameters from /Users/zoostar/Documents/git/hans_on_ml_link/saveModels/my_model_final.ckpt


In [42]:
np.allclose(best_theta, best_theta_restored)

True

---
## 9.9 텐서보드로 그래프와 학습 곡선 시각화 하기

- 훈련 과정을 log 로 남길 수 있음. <br/>


In [58]:
reset_graph()

from datetime import datetime

#  그래프가 겹치지 않도록 훈련마다 다른 로그파일로 저장
now = datetime.utcnow().strftime("%Y%m%d%H%M%S")
root_logdir = "tf_logs"
logdir = "{}/run-{}/".format(root_logdir, now)

In [66]:
n_epochs = 1000
learning_rate = 0.01
housing_target = housing.target.reshape(-1, 1)                                                       
m, n = scaled_housing_data_plus_bias.shape
print("Number of samples: {0}, Number of features: {1}".format(m, n))
print()

X = tf.placeholder(tf.float32, shape=(None, n), name="X")
y = tf.placeholder(tf.float32, shape=(None, 1), name="y")

theta = tf.Variable(
    tf.random_uniform(shape=[n, 1], minval=-1.0, maxval=1.0, seed=42), 
    name="theta"
)

y_pred = tf.matmul(X, theta, name="predictions")
error = y_pred - y
mse = tf.reduce_mean(tf.square(error), name="mse")

optimizer = tf.train.GradientDescentOptimizer(learning_rate=learning_rate)
training_op = optimizer.minimize(mse)


init = tf.global_variables_initializer()

Number of samples: 20640, Number of features: 9



In [67]:
mse_summary = tf.summary.scalar('MSE', mse) #mse 값을 평가하고 summary라는 텐서보드가 인식하는 노드를 그래프에 추가.
file_writer = tf.summary.FileWriter(logdir, tf.get_default_graph()) #로그 파일에 summary를 기록

In [77]:
n_epochs = 10
batch_size = 100
n_batches = int(np.ceil(m / batch_size))

def fetch_batch(epoch, batch_index, batch_size):
    np.random.seed(epoch * n_batches + batch_index) 
    indices = np.random.randint(m, size=batch_size) 
    X_batch = scaled_housing_data_plus_bias[indices]
    y_batch = housing.target.reshape(-1, 1)[indices]
    return X_batch, y_batch

with tf.Session() as sess:
    sess.run(init)

    for epoch in range(n_epochs):
        print("Epoch", epoch, "MSE =", mse.eval(
            feed_dict={X: scaled_housing_data_plus_bias, y: housing_target}))
        summary_str=mse_summary.eval(feed_dict={X: scaled_housing_data_plus_bias, y: housing_target})
        file_writer.add_summary(summary_str, epoch)
        for batch_index in range(n_batches):
            X_batch, y_batch = fetch_batch(epoch, batch_index, batch_size)
            sess.run(training_op, feed_dict={X: X_batch, y: y_batch})
    
    best_theta = theta.eval()
    
print("Best theta: \n{0}".format(best_theta))
         

Epoch 0 MSE = 9.161542
Epoch 1 MSE = 0.5658387
Epoch 2 MSE = 0.5529878
Epoch 3 MSE = 0.5429736
Epoch 4 MSE = 0.53469586


/anaconda3/lib/python3.6/site-packages/tensorflow/python/summary/writer/writer.py:386: UserWarning: Attempting to use a closed FileWriter. The operation will be a noop unless the FileWriter is explicitly reopened.
  warnings.warn("Attempting to use a closed FileWriter. "


Epoch 5 MSE = 0.53112817
Epoch 6 MSE = 0.53933334
Epoch 7 MSE = 0.52751964
Epoch 8 MSE = 0.52861226
Epoch 9 MSE = 0.5257666
Best theta: 
[[ 2.0703337 ]
 [ 0.8637145 ]
 [ 0.12255151]
 [-0.31211874]
 [ 0.38510373]
 [ 0.00434168]
 [-0.01232954]
 [-0.83376896]
 [-0.8030471 ]]


In [78]:
file_writer.close()

In [79]:
best_theta

array([[ 2.0703337 ],
       [ 0.8637145 ],
       [ 0.12255151],
       [-0.31211874],
       [ 0.38510373],
       [ 0.00434168],
       [-0.01232954],
       [-0.83376896],
       [-0.8030471 ]], dtype=float32)

<br/><br/>
- 텐서보드 실행 (로그파일 위치에서 tensorboard --logdir tf_logs/ 실행)
- localhost:6006

<img src="./images/zoostar/tensorboard1.png"><br/><br/>
<img src="./images/zoostar/tensorboard2.png">

---
## 9.10  이름범위

- 복잡한 모델을 다룰 때는 계산 그래프가 수천개의 노드로 구성 됨. 
- 관련 있는 노드들끼리 그룹으로 묶어 줄 필요가 있음.


In [86]:
from IPython.display import clear_output, Image, display, HTML

def strip_consts(graph_def, max_const_size=32):
    """Strip large constant values from graph_def."""
    strip_def = tf.GraphDef()
    for n0 in graph_def.node:
        n = strip_def.node.add() 
        n.MergeFrom(n0)
        if n.op == 'Const':
            tensor = n.attr['value'].tensor
            size = len(tensor.tensor_content)
            if size > max_const_size:
                tensor.tensor_content = b"<stripped %d bytes>"%size
    return strip_def

def show_graph(graph_def, max_const_size=32):
    """Visualize TensorFlow graph."""
    if hasattr(graph_def, 'as_graph_def'):
        graph_def = graph_def.as_graph_def()
    strip_def = strip_consts(graph_def, max_const_size=max_const_size)
    code = """
        <script src="//cdnjs.cloudflare.com/ajax/libs/polymer/0.3.3/platform.js"></script>
        <script>
          function load() {{
            document.getElementById("{id}").pbtxt = {data};
          }}
        </script>
        <link rel="import" href="https://tensorboard.appspot.com/tf-graph-basic.build.html" onload=load()>
        <div style="height:600px">
          <tf-graph-basic id="{id}"></tf-graph-basic>
        </div>
    """.format(data=repr(str(strip_def)), id='graph'+str(np.random.rand()))

    iframe = """
        <iframe seamless style="width:1200px;height:620px;border:0" srcdoc="{}"></iframe>
    """.format(code.replace('"', '&quot;'))
    display(HTML(iframe))
show_graph(tf.get_default_graph())

In [83]:
reset_graph()

n_epochs = 1000
learning_rate = 0.01

X = tf.placeholder(tf.float32, shape=(None, n + 1), name="X")
y = tf.placeholder(tf.float32, shape=(None, 1), name="y")
theta = tf.Variable(tf.random_uniform([n + 1, 1], -1.0, 1.0, seed=42), name="theta")
y_pred = tf.matmul(X, theta, name="predictions")
error = y_pred - y
mse = tf.reduce_mean(tf.square(error), name="mse")

In [84]:
show_graph(tf.get_default_graph())

In [87]:
reset_graph()

n_epochs = 1000
learning_rate = 0.01

X = tf.placeholder(tf.float32, shape=(None, n + 1), name="X")
y = tf.placeholder(tf.float32, shape=(None, 1), name="y")
theta = tf.Variable(tf.random_uniform([n + 1, 1], -1.0, 1.0, seed=42), name="theta")
y_pred = tf.matmul(X, theta, name="predictions")


with tf.name_scope("loss") as scope:
    error = y_pred - y
    mse = tf.reduce_mean(tf.square(error), name="mse")
    
show_graph(tf.get_default_graph())

In [82]:
# 해당 범위에는 이제 loss 라는 접두사가 붙음.
print(error.op.name)
print(mse.op.name)

sub
mse


---
## 9.11 모듈화

- ReLU <br/>
- Activation Function
<img src="https://cdn-images-1.medium.com/max/1200/1*oePAhrm74RNnNEolprmTaQ.png"/>

In [190]:
#두 개의 ReLU 출력을 더하는 그래프를 만듬.

reset_graph()

n_features = 3
X = tf.placeholder(tf.float32, shape=(None, n_features), name="X")

w1 = tf.Variable(tf.random_normal((n_features, 1)), name="weights1")
w2 = tf.Variable(tf.random_normal((n_features, 1)), name="weights2")
b1 = tf.Variable(0.0, name="bias1")
b2 = tf.Variable(0.0, name="bias2")

z1 = tf.add(tf.matmul(X, w1), b1, name="z1")
z2 = tf.add(tf.matmul(X, w2), b2, name="z2")

relu1 = tf.maximum(z1, 0., name="relu1")
relu2 = tf.maximum(z2, 0., name="relu2")  # Oops, cut&paste error! Did you spot it?

output = tf.add(relu1, relu2, name="output")

show_graph(tf.get_default_graph())

- 위 코드는 반복적인 코드가 많아 유지보수가 어렵고 에러가 발생하기 쉬움.
- ReLU를 더 추가해야한다면 더 복잡해짐.

In [195]:
reset_graph()

def relu(X):
    w_shape = (int(X.get_shape()[1]), 1)
    w = tf.Variable(tf.random_normal(w_shape), name="weights")
    b = tf.Variable(0.0, name="bias")
    z = tf.add(tf.matmul(X, w), b, name="z")
    return tf.maximum(z, 0., name="relu")

n_features = 3
X = tf.placeholder(tf.float32, shape=(None, n_features), name="X")
relus = [relu(X) for i in range(2)]
output = tf.add_n(relus, name="output")
show_graph(tf.get_default_graph())

1. 노드가 생성될 때 텐서플로우는 그 이름이 이미 존재하는지 확인.
2. 존재한다면 밑줄 다음에 숫자를 붙여 고유한 이름으로 만듬.

In [196]:
reset_graph()

a1 = tf.Variable(0, name="a")      # name == "a"
a2 = tf.Variable(0, name="a")      # name == "a_1"

with tf.name_scope("param"):       # name == "param"
    a3 = tf.Variable(2, name="a")  # name == "param/a"

with tf.name_scope("param"):       # name == "param_1"
    a4 = tf.Variable(1, name="a")  # name == "param_1/a"

for node in (a1, a2, a3, a4):
    print(node.op.name)
    
show_graph(tf.get_default_graph())

a
a_1
param/a
param_1/a


- 텐서보드는 번잡함을 줄여 좀 더 보기 좋게 보여줌<br/>
tensorboard --logdir logs/

In [96]:
reset_graph()

def relu(X):
    # relu 함수 내용을 이름범위 relu 아래에 넣어 깔끔하게 표현
    with tf.name_scope("relu"):
        w_shape = (int(X.get_shape()[1]), 1)                          
        w = tf.Variable(tf.random_normal(w_shape), name="weights")    
        b = tf.Variable(0.0, name="bias")                             
        z = tf.add(tf.matmul(X, w), b, name="z")                      
        return tf.maximum(z, 0., name="max")
    
n_features = 3
X = tf.placeholder(tf.float32, shape=(None, n_features), name="X")
relus = [relu(X) for i in range(5)]
output = tf.add_n(relus, name="output")

file_writer = tf.summary.FileWriter("logs/relu2", tf.get_default_graph())
file_writer.close()
show_graph(tf.get_default_graph())

<img src="./images/zoostar/tensorboard3.png"/>

---

## 9.12 변수공유

- 그래프의 여러 구성 요소 간 변수를 공유하고 싶을 때, 

In [97]:
# 1. 변수를 만들고, 필요한 함수에 매개변수로 전달 (사전 등으로 만들어서 사용)

reset_graph()

def relu(X, threshold):
    with tf.name_scope("relu"):
        w_shape = (int(X.get_shape()[1]), 1)                        
        w = tf.Variable(tf.random_normal(w_shape), name="weights")  
        b = tf.Variable(0.0, name="bias")                           
        z = tf.add(tf.matmul(X, w), b, name="z")                    
        return tf.maximum(z, threshold, name="max")

threshold = tf.Variable(0.0, name="threshold")
X = tf.placeholder(tf.float32, shape=(None, n_features), name="X")
relus = [relu(X, threshold) for i in range(3)]
output = tf.add_n(relus, name="output")
show_graph(tf.get_default_graph())

In [98]:
# 2. 함수 속성으로 변수 지정

reset_graph()

def relu(X):
    with tf.name_scope("relu"):
        if not hasattr(relu, "threshold"):
            relu.threshold = tf.Variable(0.0, name="threshold") # setattr(relu,tf.Variable(0.0, name="threshold"))
        w_shape = int(X.get_shape()[1]), 1                          
        w = tf.Variable(tf.random_normal(w_shape), name="weights")  
        b = tf.Variable(0.0, name="bias")                           
        z = tf.add(tf.matmul(X, w), b, name="z")                    
        return tf.maximum(z, relu.threshold, name="max")
X = tf.placeholder(tf.float32, shape=(None, n_features), name="X")
relus = [relu(X) for i in range(3)]
output = tf.add_n(relus, name="output")
show_graph(tf.get_default_graph())

In [99]:
# 3. 텐서플로우에서는 get_variable 함수를 사용해 변수가 아직 존재하지 않을 때는 새로 만들고, 이미 있을 때는 재사용 

reset_graph()

with tf.variable_scope("relu"):
    threshold = tf.get_variable("threshold", shape=(),
                                initializer=tf.constant_initializer(0.0))
    
show_graph(tf.get_default_graph())

In [90]:
#재사용 옵션이 없는 경우 에러
with tf.variable_scope("relu"):
    threshold = tf.get_variable("threshold", shape=(),
                                initializer=tf.constant_initializer(0.0))

ValueError: Variable relu/threshold already exists, disallowed. Did you mean to set reuse=True or reuse=tf.AUTO_REUSE in VarScope? Originally defined at:

  File "<ipython-input-89-1085f83fc23b>", line 7, in <module>
    initializer=tf.constant_initializer(0.0))
  File "/anaconda3/lib/python3.6/site-packages/IPython/core/interactiveshell.py", line 2910, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "/anaconda3/lib/python3.6/site-packages/IPython/core/interactiveshell.py", line 2850, in run_ast_nodes
    if self.run_code(code, result):


In [91]:
#재사용 하기1
with tf.variable_scope("relu", reuse=True):
    threshold = tf.get_variable("threshold")

In [92]:
#재사용 하기2
with tf.variable_scope("relu") as scope:
    scope.reuse_variables()
    threshold = tf.get_variable("threshold")

In [101]:
#relu()함수를 먼저 정의한 뒤, relu/threshold 변수를 생성함. 
reset_graph()
def relu(X):
    with tf.variable_scope("relu", reuse=True):
        threshold = tf.get_variable("threshold") #변수를 재사용해서 노드를 생성
        w_shape = int(X.get_shape()[1]), 1                          
        w = tf.Variable(tf.random_normal(w_shape), name="weights")  
        b = tf.Variable(0.0, name="bias")                           
        z = tf.add(tf.matmul(X, w), b, name="z")                    
        return tf.maximum(z, threshold, name="max")

X = tf.placeholder(tf.float32, shape=(None, n_features), name="X")

#함수 밖에서 threshold 변수가 정의됨 
with tf.variable_scope("relu"):
    threshold = tf.get_variable("threshold", shape=(),
                                initializer=tf.constant_initializer(0.0))
relus = [relu(X) for relu_index in range(5)]
output = tf.add_n(relus, name="output")
file_writer = tf.summary.FileWriter("logs/relu6", tf.get_default_graph())
file_writer.close()
show_graph(tf.get_default_graph())

In [102]:
#함수 안에 변수를 정의하고 싶을때, 
reset_graph()

def relu(X):
    threshold = tf.get_variable("threshold", shape=(),
                                initializer=tf.constant_initializer(0.0))
    w_shape = (int(X.get_shape()[1]), 1)                        
    w = tf.Variable(tf.random_normal(w_shape), name="weights")  
    b = tf.Variable(0.0, name="bias")                           
    z = tf.add(tf.matmul(X, w), b, name="z")                    
    return tf.maximum(z, threshold, name="max")

X = tf.placeholder(tf.float32, shape=(None, n_features), name="X")
relus = []
for relu_index in range(5):
    with tf.variable_scope("relu", reuse=(relu_index >= 1)) as scope:
        relus.append(relu(X)) #처음 생성 이후로 해당 변수를 재사용.
output = tf.add_n(relus, name="output")
file_writer = tf.summary.FileWriter("logs/relu9", tf.get_default_graph())
file_writer.close()
show_graph(tf.get_default_graph())

----
## 연습문제

#### 1. 계산을 직접 실행하지 않고 계산 그래프를 만드는 주요 장점과 단점은 무엇인가요? 

장점:<br/>
 * 텐서플로우가 자동으로 그래디언트를 계산할 수 있습니다(후진모드 자동 미분을 사용하여)
 - 텐서플로우가 여러 스레드에서 연산을 병렬로 실행할 수 있습니다. 
 - 동일한 모델을 여러 장치에 걸쳐 실행할 수 있습니다.
 - 내부 구조를 살피기 쉽습니다. 예를 들어 텐서보드에서 모델을 시각화 할 수 있습니다. 

단점:<br/>
 - 익숙하게 다루려면 시간이 필요합니다.
 - 단계별 디버깅을 수행하기 어렵습니다. (구성단계, 실행단계로 나뉨)
 

#### 2. a_val = a.eval(session=sess) 와 a_val = sess.run(a)는 동일한 문장인가요?

In [24]:
reset_graph()
a = tf.Variable(3, name="x")
sess = tf.Session()
sess.run(a.initializer)
a_val = a.eval(session=sess)
print(a_val)
sess.close()

3


In [25]:
reset_graph()
a = tf.Variable(3, name="x")
sess = tf.Session()
sess.run(a.initializer)
a_val = sess.run(a)
print(a_val)
sess.close()

3


동일합니다.

#### 3. a_val, b_val = a.eval(session=sess), b.eval(session=sess)와 a_val, b_val = sess.run([a,b])는 동일한 문장인가요?

- a_val, b_val = a.eval(session=sess), b.eval(session=sess) <br/>
 : 그래프를 두 번 실행합니다. (a계산,b계산)
- a_val, b_val = sess.run([a,b]) <br/>
 : 그래프를 한 번 실행합니다.
 
a_val, b_val = sess.run([a,b]) 이 더 빨리 실행됩니다.

In [26]:
import time
start_time = time.time() 

reset_graph()
a = tf.Variable(3, name="x")
b = tf.Variable(4, name="x")
sess = tf.Session()
sess.run(a.initializer)
sess.run(b.initializer)
a_val, b_val = a.eval(session=sess), b.eval(session=sess)
print(a_val)
print(b_val)

print("--- %s seconds ---" %(time.time() - start_time))
sess.close()

3
4
--- 0.009422063827514648 seconds ---


In [27]:
start_time = time.time() 
reset_graph()
a = tf.Variable(3, name="x")
b = tf.Variable(4, name="x")
init = tf.global_variables_initializer()
sess = tf.Session()
sess.run(init)
a_val, b_val = sess.run([a,b])
print(a_val)
print(b_val)

print("--- %s seconds ---" %(time.time() - start_time))
sess.close()

3
4
--- 0.008866071701049805 seconds ---


#### 4. 같은 세션에서 두 개의 그래프를 실행 할 수 있나요?

- 같은 세션에서 두 개의 그래프를 실행할 수 없습니다. 두 개의 그래프를 하나로 합쳐야합니다.

#### 5. 만약 변수 w를 가진 그래프 g를 만들고 스레드 두 개를 시작해 각 스레드에서 동일한 그래프 g를 사용하는 세션을 열면, 각 세션은 변수 w를 따로 가지게 될까요? 아니면 공유할까요? 

- 로컬 텐서플로우에서는 세션이 변수값을 관리하므로 각 세션은 변수 w의 복사본을 각자 가지게 될 것입니다. 하지만 분산 텐서플로우에서는 클러스터의 컨테이너에서 변수 값이 관리되므로 같은 컨테이너를 사용하면 동일한 변수를 공유할 것입니다.

#### 6. 변수는 언제 초기화가 되고 언제 소멸되나요?

- 변수는 함수가 호출 될 때 초기화 되고, 세션이 종료될 때 소멸됩니다. 하지만 분산텐서플로우에서는 컨테이너를 리셋해야합니다.

#### 7.플레이스홀더와 변수의 차이점은 무엇인가요?

In [24]:
import tensorflow as tf

x = tf.Variable(5)
X = tf.placeholder(tf.float32, shape=(), name="X")

init = tf.global_variables_initializer()
with tf.Session() as sess:
    sess.run(init)
    print(x.eval())
    print(X.eval(feed_dict={X:"4"}))
#     print(X.eval())

5
4.0


- 변수는 값을 가진 연산이고, 변수를 실행하면 값이 반환됩니다. 따라서 변수는 실행하기전 초기화해야합니다. <br/>
  주로 변수는 훈련 스텝의 카운트나 모델 파라미터를 저장하기 위해 사용됩니다.
- 플레이스홀더는 표현하려는 텐서의 크기와 타입에 관한 정보만 가지고 있을 뿐 아무런 값도 가지고 있지 않습니다.<br/>
  실제로 플레이스홀더에 의존하고 있는 연산을 평가하려면 플레이스홀더의 값을 (feed_dict 매개변수)로 텐서플로우에 넣어주어야합니다. <br/>
  일반적으로 실행 단계에서 훈련, 테스트 데이터를 주입할 때 사용됩니다. 

#### 8.플레이스홀더에 의존하는 연산을 평가하기 위해 그래프를 실행할 때 플레이스홀더에 값을 주입하지 않으면 어떻게 될까요? 플레이스홀더에 의존하지 않는 연산이라면 어떻게 될까요?

- 플레이스홀더에 의존하는 연산이라면 예외가 발생됩니다.

#### 9. 그래프를 실행할 때 어떤 연산자의 출력 값을 주입할 수 있나요? 아니면 플레이스홀더의 값만 가능한가요?

- 플레이스홀더 뿐만 아니라 어떤 연산의 출력 값도 주입할 수 있습니다. 하지만 이는 실제로는 매우 드문 경우입니다. 

#### 10. (실행단계에서) 변수에 원하는 값을 어떻게 설정할 수 있나요?

In [5]:
import tensorflow as tf

x = tf.Variable(tf.random_uniform(shape=(),minval=0.0,maxval=0.0))
x_new_val = tf.placeholder(tf.float32, shape=())
x_assign = tf.assign(x,x_new_val) #tf.assign() 함수를 활용해 할당 노드를 만들고 실행단계에서 주입할 예정

with tf.Session():
    x.initializer.run() 
    print(x.eval())
    x_assign.eval(feed_dict={x_new_val:5.0}) #플레이스홀더를 사용해 변수에 값 할당
    print(x.eval())

0.0
5.0


#### 11. 후진 모드 자동 미분으로 변수 10개에 대한 비용 함수의 그래디언트를 계산하려면 그래프를 몇 번 순회해야 하나요? 전진 모드 자동 미분이나 기호 미분의 경우는 어떨까요?

- 후진모드 자동미분은 변수 개수에 상관없이 변수에 대한 비용함수와 그래디언트를 계산하기 위해 그래프를 두번 순회해야합니다.
- 반면, 전진모드 자동 미분은 각 변수마다 실행해야하므로 10번 실행햐애합니다. 
- 기호 미분은 그래디언트 계산을 위해 다른 그래프를 만들기 때문에 원본 그래프를 순회하지 않습니다.

#### 12. 텐서플로우를 사용해 미니배치 경사 하강법으로 로지스틱 회귀를 구현해보세요.

In [3]:
from sklearn.datasets import make_moons
import numpy as np
import tensorflow as tf

m = 1000
X_moons, y_moons = make_moons(m, noise=0.1, random_state=42)
X_moons_with_bias = np.c_[np.ones((m, 1)), X_moons]
y_moons_column_vector = y_moons.reshape(-1, 1)

test_ratio = 0.2
test_size = int(m * test_ratio)
X_train = X_moons_with_bias[:-test_size]
X_test = X_moons_with_bias[-test_size:]
y_train = y_moons_column_vector[:-test_size]
y_test = y_moons_column_vector[-test_size:]

def random_batch(X_train, y_train, batch_size):
    rnd_indices = np.random.randint(0, len(X_train), batch_size)
    X_batch = X_train[rnd_indices]
    y_batch = y_train[rnd_indices]
    return X_batch, y_batch

reset_graph()
n_inputs = 2

X = tf.placeholder(tf.float32, shape=(None, n_inputs + 1), name="X")
y = tf.placeholder(tf.float32, shape=(None, 1), name="y")
theta = tf.Variable(tf.random_uniform([n_inputs + 1, 1], -1.0, 1.0, seed=42), name="theta")
logits = tf.matmul(X, theta, name="logits")
y_proba = 1 / (1 + tf.exp(-logits))
# y_proba = tf.sigmoid(logits)

epsilon = 1e-7  # 로그를 계산할 때 오버플로우를 피하기 위해
loss = -tf.reduce_mean(y * tf.log(y_proba + epsilon) + (1 - y) * tf.log(1 - y_proba + epsilon))

loss = tf.losses.log_loss(y, y_proba)  # 기본적으로 epsilon = 1e-7 가 사용됩니다

learning_rate = 0.01
optimizer = tf.train.GradientDescentOptimizer(learning_rate=learning_rate)
training_op = optimizer.minimize(loss)

init = tf.global_variables_initializer()

n_epochs = 1000
batch_size = 50
n_batches = int(np.ceil(m / batch_size))

with tf.Session() as sess:
    sess.run(init)

    for epoch in range(n_epochs):
        for batch_index in range(n_batches):
            X_batch, y_batch = random_batch(X_train, y_train, batch_size)
            sess.run(training_op, feed_dict={X: X_batch, y: y_batch})
        loss_val = loss.eval({X: X_test, y: y_test})
        if epoch % 100 == 0:
            print("에포크:", epoch, "\tLoss:", loss_val)

    y_proba_val = y_proba.eval(feed_dict={X: X_test, y: y_test})


Instructions for updating:
Use tf.cast instead.
에포크: 0 	Loss: 0.79260236
에포크: 100 	Loss: 0.3434635
에포크: 200 	Loss: 0.30754045
에포크: 300 	Loss: 0.29288894
에포크: 400 	Loss: 0.28533572
에포크: 500 	Loss: 0.28047806
에포크: 600 	Loss: 0.27808294
에포크: 700 	Loss: 0.2761544
에포크: 800 	Loss: 0.27551997
에포크: 900 	Loss: 0.27491233


In [4]:
# 재사용 가능하도록
def logistic_regression(X, y, initializer=None, seed=42, learning_rate=0.01):
    n_inputs_including_bias = int(X.get_shape()[1])
    with tf.name_scope("logistic_regression"):
        with tf.name_scope("model"):
            if initializer is None:
                initializer = tf.random_uniform([n_inputs_including_bias, 1], -1.0, 1.0, seed=seed)
            theta = tf.Variable(initializer, name="theta")
            logits = tf.matmul(X, theta, name="logits")
            y_proba = tf.sigmoid(logits)
        with tf.name_scope("train"):
            loss = tf.losses.log_loss(y, y_proba, scope="loss")
            optimizer = tf.train.GradientDescentOptimizer(learning_rate=learning_rate)
            training_op = optimizer.minimize(loss)
            loss_summary = tf.summary.scalar('log_loss', loss)
        with tf.name_scope("init"):
            init = tf.global_variables_initializer()
        with tf.name_scope("save"): 
            saver = tf.train.Saver()
    return y_proba, loss, training_op, loss_summary, init, saver


In [7]:
#로그 생성 및 함수 실행
reset_graph()
from datetime import datetime

def log_dir(prefix=""):
    now = datetime.utcnow().strftime("%Y%m%d%H%M%S")
    root_logdir = "tf_logs"
    if prefix:
        prefix += "-"
    name = prefix + "run-" + now
    return "{}/{}/".format(root_logdir, name)

n_inputs = 2 + 4 #특성 추가
logdir = log_dir("logreg")

X = tf.placeholder(tf.float32, shape=(None, n_inputs + 1), name="X")
y = tf.placeholder(tf.float32, shape=(None, 1), name="y")

y_proba, loss, training_op, loss_summary, init, saver = logistic_regression(X, y)

file_writer = tf.summary.FileWriter(logdir, tf.get_default_graph())

show_graph(tf.get_default_graph())

In [8]:
#입력에 x12, x22, x13 그리고 x23 네 개의 특성을 추가합니다. 
#특성을 추가하면 모델의 성능이 향상되는 것을 확인할 수 있습니다. 
X_train_enhanced = np.c_[X_train,
                         np.square(X_train[:, 1]),
                         np.square(X_train[:, 2]),
                         X_train[:, 1] ** 3,
                         X_train[:, 2] ** 3]
X_test_enhanced = np.c_[X_test,
                        np.square(X_test[:, 1]),
                        np.square(X_test[:, 2]),
                        X_test[:, 1] ** 3,
                        X_test[:, 2] ** 3]

X_train_enhanced[:5]

array([[ 1.00000000e+00, -5.14696757e-02,  4.44198631e-01,
         2.64912752e-03,  1.97312424e-01, -1.36349734e-04,
         8.76459084e-02],
       [ 1.00000000e+00,  1.03201691e+00, -4.19741157e-01,
         1.06505890e+00,  1.76182639e-01,  1.09915879e+00,
        -7.39511049e-02],
       [ 1.00000000e+00,  8.67891864e-01, -2.54827114e-01,
         7.53236288e-01,  6.49368582e-02,  6.53727646e-01,
        -1.65476722e-02],
       [ 1.00000000e+00,  2.88850997e-01, -4.48668621e-01,
         8.34348982e-02,  2.01303531e-01,  2.41002535e-02,
        -9.03185778e-02],
       [ 1.00000000e+00, -8.33439108e-01,  5.35056649e-01,
         6.94620746e-01,  2.86285618e-01, -5.78924095e-01,
         1.53179024e-01]])

In [10]:
save_dir = "/Users/zoostar/Documents/git/hans_on_ml_link/saveModels/"

In [11]:
n_epochs = 10001
batch_size = 50
n_batches = int(np.ceil(m / batch_size))

checkpoint_path = save_dir+"my_logreg_model.ckpt"
checkpoint_epoch_path = checkpoint_path + ".epoch"
final_model_path = save_dir+"my_logreg_model"

with tf.Session() as sess:
    if os.path.isfile(checkpoint_epoch_path):
        # 체크포인트 파일이 있으면 모델을 복원하고 에포크 횟수를 로드합니다
        with open(checkpoint_epoch_path, "rb") as f:
            start_epoch = int(f.read())
        print("중지되었던 훈련입니다. 에포크를 이어갑니다.", start_epoch)
        saver.restore(sess, checkpoint_path)
    else:
        start_epoch = 0
        sess.run(init)

    for epoch in range(start_epoch, n_epochs):
        for batch_index in range(n_batches):
            X_batch, y_batch = random_batch(X_train_enhanced, y_train, batch_size)
            sess.run(training_op, feed_dict={X: X_batch, y: y_batch})
        loss_val, summary_str = sess.run([loss, loss_summary], feed_dict={X: X_test_enhanced, y: y_test})
        file_writer.add_summary(summary_str, epoch)
        if epoch % 500 == 0:
            print("에포크:", epoch, "\t손실:", loss_val)
            saver.save(sess, checkpoint_path)
            with open(checkpoint_epoch_path, "wb") as f:
                f.write(b"%d" % (epoch + 1))

    saver.save(sess, final_model_path)
    y_proba_val = y_proba.eval(feed_dict={X: X_test_enhanced, y: y_test})
    os.remove(checkpoint_epoch_path)

중지되었던 훈련입니다. 에포크를 이어갑니다. 501
Instructions for updating:
Use standard file APIs to check for files with this prefix.
INFO:tensorflow:Restoring parameters from /Users/zoostar/Documents/git/hans_on_ml_link/saveModels/my_logreg_model.ckpt
에포크: 1000 	손실: 0.035854872
에포크: 1500 	손실: 0.027411753
에포크: 2000 	손실: 0.023843646
에포크: 2500 	손실: 0.021728296
에포크: 3000 	손실: 0.020410137
에포크: 3500 	손실: 0.019330766
에포크: 4000 	손실: 0.018541276
에포크: 4500 	손실: 0.017897042
에포크: 5000 	손실: 0.017266024
에포크: 5500 	손실: 0.01678276
에포크: 6000 	손실: 0.016404107
에포크: 6500 	손실: 0.016048055
에포크: 7000 	손실: 0.015632374
에포크: 7500 	손실: 0.01536644
에포크: 8000 	손실: 0.015050891
에포크: 8500 	손실: 0.014815379
에포크: 9000 	손실: 0.0145947365
에포크: 9500 	손실: 0.014360069
에포크: 10000 	손실: 0.01413806


In [ ]:
## 파라미터 변경

from scipy.stats import reciprocal

n_search_iterations = 10

for search_iteration in range(n_search_iterations):
    batch_size = np.random.randint(1, 100)
    learning_rate = reciprocal(0.0001, 0.1).rvs(random_state=search_iteration)

    n_inputs = 2 + 4
    logdir = log_dir("logreg")
    
    print("반복", search_iteration)
    print("  logdir:", logdir)
    print("  batch_size:", batch_size)
    print("  learning_rate:", learning_rate)
    print("  훈련: ", end="")

    reset_graph()

    X = tf.placeholder(tf.float32, shape=(None, n_inputs + 1), name="X")
    y = tf.placeholder(tf.float32, shape=(None, 1), name="y")

    y_proba, loss, training_op, loss_summary, init, saver = logistic_regression(
        X, y, learning_rate=learning_rate)

    file_writer = tf.summary.FileWriter(logdir, tf.get_default_graph())

    n_epochs = 10001
    n_batches = int(np.ceil(m / batch_size))

    final_model_path = "./my_logreg_model_%d" % search_iteration

    with tf.Session() as sess:
        sess.run(init)

        for epoch in range(n_epochs):
            for batch_index in range(n_batches):
                X_batch, y_batch = random_batch(X_train_enhanced, y_train, batch_size)
                sess.run(training_op, feed_dict={X: X_batch, y: y_batch})
            loss_val, summary_str = sess.run([loss, loss_summary], feed_dict={X: X_test_enhanced, y: y_test})
            file_writer.add_summary(summary_str, epoch)
            if epoch % 500 == 0:
                print(".", end="")

        saver.save(sess, final_model_path)

        print()
        y_proba_val = y_proba.eval(feed_dict={X: X_test_enhanced, y: y_test})
        y_pred = (y_proba_val >= 0.5)
        
        print("  정밀도:", precision_score(y_test, y_pred))
        print("  재현율:", recall_score(y_test, y_pred))

반복 0
  logdir: tf_logs/logreg-run-20190319034622/
  batch_size: 12
  learning_rate: 0.004430375245218265
  훈련: ..

----
### 지난 주 실습 코드

In [6]:
import tensorflow as tf
# 공통
import numpy as np
import os
from sklearn.datasets import fetch_california_housing

# 일관된 출력을 위해 유사난수 초기화
def reset_graph(seed=42):
    tf.reset_default_graph()
    tf.set_random_seed(seed)
    np.random.seed(seed)

# 맷플롯립 설정
%matplotlib inline
import matplotlib
import matplotlib.pyplot as plt
plt.rcParams['axes.labelsize'] = 14
plt.rcParams['xtick.labelsize'] = 12
plt.rcParams['ytick.labelsize'] = 12

# 한글출력
plt.rcParams['font.family'] = 'NanumBarunGothic'
plt.rcParams['axes.unicode_minus'] = False

# 그림을 저장할 폴더
PROJECT_ROOT_DIR = "."
CHAPTER_ID = "tensorflow"

def save_fig(fig_id, tight_layout=True):
    path = os.path.join(PROJECT_ROOT_DIR, "images", CHAPTER_ID, fig_id + ".png")
    if tight_layout:
        plt.tight_layout()
    plt.savefig(path, format='png', dpi=300)
    
reset_graph()

x = tf.Variable(3, name="x")
y = tf.Variable(4, name="y")
f = x*x*y + y + 2

sess = tf.Session()
sess.run(x.initializer)
sess.run(y.initializer)
result = sess.run(f)

sess.close()

with tf.Session() as sess:
    x.initializer.run()
    y.initializer.run()
    result = f.eval()
    
init = tf.global_variables_initializer()

with tf.Session() as sess:
    init.run()
    result = f.eval()
    
init = tf.global_variables_initializer()

sess = tf.InteractiveSession()
init.run()
result = f.eval()

sess.close()

reset_graph()

x1 = tf.Variable(1)
x1.graph is tf.get_default_graph()


graph = tf.Graph()
with graph.as_default():
    x2 = tf.Variable(2)
    
w = tf.constant(3)
x = w + 2
y = x + 5
z = x * 3

with tf.Session() as sess:
    print(y.eval())  # 10
    print(z.eval())  # 15
    
    
with tf.Session() as sess:
    y_val, z_val = sess.run([y, z])
    print(y_val)  # 10
    print(z_val)  # 15\

reset_graph()

housing = fetch_california_housing()
m, n = housing.data.shape
housing_data_plus_bias = np.c_[np.ones((m, 1)), housing.data]

X = tf.constant(housing_data_plus_bias, dtype=tf.float32, name="X")
y = tf.constant(housing.target.reshape(-1, 1), dtype=tf.float32, name="y")
XT = tf.transpose(X)
theta = tf.matmul(tf.matmul(tf.matrix_inverse(tf.matmul(XT, X)), XT), y)

with tf.Session() as sess:
    theta_value = theta.eval()

X = housing_data_plus_bias
y = housing.target.reshape(-1, 1)
theta_numpy = np.linalg.inv(X.T.dot(X)).dot(X.T).dot(y)

from sklearn.linear_model import LinearRegression
lin_reg = LinearRegression()
lin_reg.fit(housing.data, housing.target.reshape(-1, 1))

from sklearn.preprocessing import StandardScaler
scaler = StandardScaler()
scaled_housing_data = scaler.fit_transform(housing.data)
scaled_housing_data_plus_bias = np.c_[np.ones((m, 1)), scaled_housing_data]


reset_graph()

n_epochs = 1000
learning_rate = 0.01

X = tf.constant(scaled_housing_data_plus_bias, dtype=tf.float32, name="X")
y = tf.constant(housing.target.reshape(-1, 1), dtype=tf.float32, name="y")
theta = tf.Variable(tf.random_uniform([n + 1, 1], -1.0, 1.0, seed=42), name="theta")
y_pred = tf.matmul(X, theta, name="predictions")
error = y_pred - y
mse = tf.reduce_mean(tf.square(error), name="mse")
gradients = 2/m * tf.matmul(tf.transpose(X), error)
training_op = tf.assign(theta, theta - learning_rate * gradients)

init = tf.global_variables_initializer()

with tf.Session() as sess:
    sess.run(init)

    for epoch in range(n_epochs):
        if epoch % 100 == 0:
            print("에포크", epoch, "MSE =", mse.eval())
        sess.run(training_op)
    
    best_theta = theta.eval()
    
reset_graph()

n_epochs = 1000
learning_rate = 0.01

X = tf.constant(scaled_housing_data_plus_bias, dtype=tf.float32, name="X")
y = tf.constant(housing.target.reshape(-1, 1), dtype=tf.float32, name="y")
theta = tf.Variable(tf.random_uniform([n + 1, 1], -1.0, 1.0, seed=42), name="theta")
y_pred = tf.matmul(X, theta, name="predictions")
error = y_pred - y
mse = tf.reduce_mean(tf.square(error), name="mse")

gradients = tf.gradients(mse, [theta])[0]

training_op = tf.assign(theta, theta - learning_rate * gradients)

init = tf.global_variables_initializer()

with tf.Session() as sess:
    sess.run(init)

    for epoch in range(n_epochs):
        if epoch % 100 == 0:
            print("에포크", epoch, "MSE =", mse.eval())
        sess.run(training_op)
    
    best_theta = theta.eval()
    
def my_func(a, b):
    z = 0
    for i in range(100):
        z = a * np.cos(z + i) + z * np.sin(b - i)
    return z


reset_graph()

a = tf.Variable(0.2, name="a")
b = tf.Variable(0.3, name="b")
z = tf.constant(0.0, name="z0")
for i in range(100):
    z = a * tf.cos(z + i) + z * tf.sin(b - i)

grads = tf.gradients(z, [a, b])
init = tf.global_variables_initializer()

with tf.Session() as sess:
    init.run()
    print(z.eval())
    print(sess.run(grads))
    
reset_graph()

n_epochs = 1000
learning_rate = 0.01

X = tf.constant(scaled_housing_data_plus_bias, dtype=tf.float32, name="X")
y = tf.constant(housing.target.reshape(-1, 1), dtype=tf.float32, name="y")
theta = tf.Variable(tf.random_uniform([n + 1, 1], -1.0, 1.0, seed=42), name="theta")
y_pred = tf.matmul(X, theta, name="predictions")
error = y_pred - y
mse = tf.reduce_mean(tf.square(error), name="mse")

optimizer = tf.train.GradientDescentOptimizer(learning_rate=learning_rate)
training_op = optimizer.minimize(mse)

init = tf.global_variables_initializer()

with tf.Session() as sess:
    sess.run(init)

    for epoch in range(n_epochs):
        if epoch % 100 == 0:
            print("에포크", epoch, "MSE =", mse.eval())
        sess.run(training_op)
    
    best_theta = theta.eval()
    
    
reset_graph()

n_epochs = 1000
learning_rate = 0.01

X = tf.constant(scaled_housing_data_plus_bias, dtype=tf.float32, name="X")
y = tf.constant(housing.target.reshape(-1, 1), dtype=tf.float32, name="y")
theta = tf.Variable(tf.random_uniform([n + 1, 1], -1.0, 1.0, seed=42), name="theta")
y_pred = tf.matmul(X, theta, name="predictions")
error = y_pred - y
mse = tf.reduce_mean(tf.square(error), name="mse")

optimizer = tf.train.MomentumOptimizer(learning_rate=learning_rate,
                                       momentum=0.9)

training_op = optimizer.minimize(mse)

init = tf.global_variables_initializer()

with tf.Session() as sess:
    sess.run(init)

    for epoch in range(n_epochs):
        sess.run(training_op)
    
    best_theta = theta.eval()

    
reset_graph()

A = tf.placeholder(tf.float32, shape=(None, 3))
B = A + 5
with tf.Session() as sess:
    B_val_1 = B.eval(feed_dict={A: [[1, 2, 3]]})
    B_val_2 = B.eval(feed_dict={A: [[4, 5, 6], [7, 8, 9]]})

print(B_val_1)

n_epochs = 1000
learning_rate = 0.01

reset_graph()

X = tf.placeholder(tf.float32, shape=(None, n + 1), name="X")
y = tf.placeholder(tf.float32, shape=(None, 1), name="y")

theta = tf.Variable(tf.random_uniform([n + 1, 1], -1.0, 1.0, seed=42), name="theta")
y_pred = tf.matmul(X, theta, name="predictions")
error = y_pred - y
mse = tf.reduce_mean(tf.square(error), name="mse")
optimizer = tf.train.GradientDescentOptimizer(learning_rate=learning_rate)
training_op = optimizer.minimize(mse)

init = tf.global_variables_initializer()

n_epochs = 10

batch_size = 100
n_batches = int(np.ceil(m / batch_size))

def fetch_batch(epoch, batch_index, batch_size):
    np.random.seed(epoch * n_batches + batch_index)  # not shown in the book
    indices = np.random.randint(m, size=batch_size)  # not shown
    X_batch = scaled_housing_data_plus_bias[indices] # not shown
    y_batch = housing.target.reshape(-1, 1)[indices] # not shown
    return X_batch, y_batch

with tf.Session() as sess:
    sess.run(init)

    for epoch in range(n_epochs):
        for batch_index in range(n_batches):
            X_batch, y_batch = fetch_batch(epoch, batch_index, batch_size)
            sess.run(training_op, feed_dict={X: X_batch, y: y_batch})

    best_theta = theta.eval()
    
from IPython.display import clear_output, Image, display, HTML

def strip_consts(graph_def, max_const_size=32):
    """Strip large constant values from graph_def."""
    strip_def = tf.GraphDef()
    for n0 in graph_def.node:
        n = strip_def.node.add() 
        n.MergeFrom(n0)
        if n.op == 'Const':
            tensor = n.attr['value'].tensor
            size = len(tensor.tensor_content)
            if size > max_const_size:
                tensor.tensor_content = b"<stripped %d bytes>"%size
    return strip_def

def show_graph(graph_def, max_const_size=32):
    """Visualize TensorFlow graph."""
    if hasattr(graph_def, 'as_graph_def'):
        graph_def = graph_def.as_graph_def()
    strip_def = strip_consts(graph_def, max_const_size=max_const_size)
    code = """
        <script src="//cdnjs.cloudflare.com/ajax/libs/polymer/0.3.3/platform.js"></script>
        <script>
          function load() {{
            document.getElementById("{id}").pbtxt = {data};
          }}
        </script>
        <link rel="import" href="https://tensorboard.appspot.com/tf-graph-basic.build.html" onload=load()>
        <div style="height:600px">
          <tf-graph-basic id="{id}"></tf-graph-basic>
        </div>
    """.format(data=repr(str(strip_def)), id='graph'+str(np.random.rand()))

    iframe = """
        <iframe seamless style="width:1200px;height:620px;border:0" srcdoc="{}"></iframe>
    """.format(code.replace('"', '&quot;'))
    display(HTML(iframe))
show_graph(tf.get_default_graph())

10
15
10
15
에포크 0 MSE = 9.161542
에포크 100 MSE = 0.71450055
에포크 200 MSE = 0.56670487
에포크 300 MSE = 0.55557173
에포크 400 MSE = 0.5488112
에포크 500 MSE = 0.5436363
에포크 600 MSE = 0.53962904
에포크 700 MSE = 0.5365092
에포크 800 MSE = 0.53406775
에포크 900 MSE = 0.5321473
에포크 0 MSE = 9.161542
에포크 100 MSE = 0.7145004
에포크 200 MSE = 0.56670487
에포크 300 MSE = 0.55557173
에포크 400 MSE = 0.5488112
에포크 500 MSE = 0.5436363
에포크 600 MSE = 0.53962904
에포크 700 MSE = 0.5365092
에포크 800 MSE = 0.53406775
에포크 900 MSE = 0.5321473
-0.21253741
[-1.1388494, 0.19671395]
에포크 0 MSE = 9.161542
에포크 100 MSE = 0.7145004
에포크 200 MSE = 0.56670487
에포크 300 MSE = 0.55557173
에포크 400 MSE = 0.5488112
에포크 500 MSE = 0.5436363
에포크 600 MSE = 0.53962904
에포크 700 MSE = 0.5365092
에포크 800 MSE = 0.53406775
에포크 900 MSE = 0.5321473
[[6. 7. 8.]]
